In [2]:
# data manipulation
import numpy as np
import pandas as pd

#file processing / requests
from pathlib import Path
from tqdm import tqdm
import json
import urllib

#computer vision
import cv2
import torch
import torchvision

import PIL

#ML 
from sklearn.model_selection import train_test_split


#display
from IPython.display import display
from pylab import rcParams

#visualization
import seaborn as sns
import matplotlib.pyplot as plt
from matplotlib import rc
import PIL.Image as Image

from IPython.core.display import display, HTML
display(HTML("<style>.container { width:100% !important; }</style>"))
pd.set_option('display.max_columns', None)

In [3]:
import torch
print(torch.cuda.is_available())
print(torch.cuda.current_device())
print(torch.cuda.device_count())
print(torch.cuda.get_device_name(0))

True
0
1
NVIDIA GeForce RTX 3090


In [ ]:
## Following https://towardsdatascience.com/building-your-own-object-detector-pytorch-vs-tensorflow-and-how-to-even-get-started-1d314691d4ae

In [4]:
import pycocotools

In [3]:
import sys
sys.path.append('/Users/Administrator/DS/DeepRoad/Object_Detection')
sys.path.append('/Users/phil0/DS/DeepRoad/Object_Detection')
import utils2
from importlib import reload
reload(utils2)
from utils2 import *

xmls = pd.read_csv('train/ieee_dataset_1210.csv', sep = ',')
xmls = dropcol(xmls)
print(xmls.shape)
print(xmls['class'].unique())
xmls['class'] = np.where((xmls['class'] == 'Longitudinal Crack'), 1, np.where((xmls['class'] == 'Lateral Crack'), 2, np.where(xmls['class'] == 'Alligator Crack', 3, 4)))
xmls['area'] = (xmls['ymax'].astype(int) - xmls['ymin'].astype(int)) * (xmls['xmax'].astype(int) - xmls['xmin'].astype(int))
xmls

NOTE! Installing ujson may make loading annotations faster.
(25046, 9)
['Longitudinal Crack' 'Pothole' 'Lateral Crack' 'Alligator Crack']


filename  width  height  class  xmin  ymin  xmax  ymax   area
0      Czech_000006.jpg    600     600      1   141   405   166   472   1675
1      Czech_000010.jpg    600     600      4   213   409   274   441   1952
2      Czech_000010.jpg    600     600      2   228   473   327   495   2178
3      Czech_000020.jpg    600     600      2    97   477   167   499   1540
4      Czech_000020.jpg    600     600      2   110   443   180   465   1540
...                 ...    ...     ...    ...   ...   ...   ...   ...    ...
25041  Japan_013125.jpg    600     600      2   286   370   419   397   3591
25042  Japan_013129.jpg    600     600      1   195   446   225   491   1350
25043  Japan_013131.jpg    600     600      3   475   505   565   543   3420
25044  Japan_013132.jpg    600     600      1   542   275   600   336   3538
25045  Japan_013132.jpg    600     600      3   244   159   336   414  23460

[25046 rows x 9 columns]

In [14]:
import os
import numpy as np
import torch
import torch.utils.data
from PIL import Image
import pandas as pd
from torchvision.models.detection.faster_rcnn import FastRCNNPredictor
from engine import train_one_epoch, evaluate
import utils
import transforms as T


def parse_one_annot(path_to_data_file, filename):
    data = pd.read_csv(path_to_data_file)
    boxes_array = data[data["filename"] == filename][["xmin", "ymin","xmax", "ymax"]].values
    return boxes_array


def parse_labels(path_to_data_file, filename):
    data = pd.read_csv(path_to_data_file)
    labels_array = data[data["filename"] == filename][["class"]].values
    labels_array = [item for sublist in labels_array for item in sublist]
    return labels_array


class TorchDataset(torch.utils.data.Dataset):
    def __init__(self, root, data_file, transforms=None):
        self.root = root
        self.transforms = transforms
        self.imgs = sorted(os.listdir(os.path.join(root, "images")))
        self.path_to_data_file = data_file
    def __getitem__(self, idx):
       # load images and bounding boxes
        img_path = os.path.join(self.root, "images", self.imgs[idx])
        img = Image.open(img_path).convert("RGB")
        box_list = parse_one_annot(self.path_to_data_file, self.imgs[idx])
        boxes = torch.as_tensor(box_list, dtype=torch.float32)
        num_objs = len(box_list)
        # pulling labels for each image 
        labels_list = parse_labels(self.path_to_data_file, self.imgs[idx])
        labels = torch.as_tensor(labels_list, dtype=torch.int64) 
        #labels = torch.ones((num_objs,), dtype=torch.int64)
        image_id = torch.tensor([idx])
        area = (boxes[:, 3] - boxes[:, 1]) * (boxes[:, 2] - boxes[:,0])
        # suppose all instances are not crowd
        iscrowd = torch.zeros((num_objs,), dtype=torch.int64)
        target = {}
        target["boxes"] = boxes
        target["labels"] = labels
        target["image_id"] = image_id
        target["area"] = area
        target["iscrowd"] = iscrowd
        transform = torchvision.transforms.Compose([torchvision.transforms.ToTensor()])
        if self.transforms is not None:
            img, target = torchvision.transforms.Compose([torchvision.transforms.ToTensor()])(img, target)
        return transform(img), target
    def __len__(self):
        return len(self.imgs)
# transform = transforms.Compose([
#     transforms.ToPILImage(),
#     transforms.RandomAffine(degrees = 10, translate = (0.1, 0.1), scale = (.8, 1.2)),
#     transforms.ToTensor(),
#     transforms.RandomErasing(p=1,scale=(0.02, 0.05))
# ])
transform= torchvision.transforms.Compose([torchvision.transforms.ToTensor()]) #torchvision.transforms.ToPILImage(), 
dataset3 = TorchDataset(root = 'train', data_file= 'train/ieee_dataset_1210_2.csv', transforms = None)

In [9]:
img, target = dataset3.__getitem__(0)
print(img, target)

torch.manual_seed(1)
indices = torch.randperm(len(dataset3)).tolist()
# valindices = torch.randperm(valmask).tolist()
# trainindices = torch.randperm(trainmask).tolist()
dataset3 = torch.utils.data.Subset(dataset3, indices[:-420])
dataset3_test = torch.utils.data.Subset(dataset3, indices[-420:])

# define training and validation data loaders
data_loader3 = torch.utils.data.DataLoader(
              dataset3, batch_size=8, shuffle=True, num_workers=0,
              collate_fn=utils.collate_fn)
data_loader3_test = torch.utils.data.DataLoader(
         dataset3_test, batch_size=1, shuffle=False, num_workers=0,
         collate_fn=utils.collate_fn)
print("We have: {} examples, {} are training and {} testing".format(len(indices), len(dataset3), len(dataset3_test)))

tensor([[[0.4235, 0.4196, 0.4078,  ..., 0.8196, 0.8157, 0.8157],
         [0.3922, 0.3804, 0.3647,  ..., 0.8157, 0.8157, 0.8157],
         [0.3882, 0.3686, 0.3412,  ..., 0.8157, 0.8157, 0.8157],
         ...,
         [0.0000, 0.0000, 0.0000,  ..., 0.0941, 0.0980, 0.0941],
         [0.0039, 0.0000, 0.0039,  ..., 0.0471, 0.0549, 0.0588],
         [0.0118, 0.0078, 0.0118,  ..., 0.0353, 0.0471, 0.0588]],

        [[0.4863, 0.4863, 0.4745,  ..., 0.8941, 0.8902, 0.8902],
         [0.4549, 0.4431, 0.4314,  ..., 0.8902, 0.8902, 0.8902],
         [0.4510, 0.4314, 0.4078,  ..., 0.8902, 0.8902, 0.8902],
         ...,
         [0.0157, 0.0118, 0.0157,  ..., 0.0980, 0.1020, 0.0980],
         [0.0078, 0.0039, 0.0078,  ..., 0.0588, 0.0667, 0.0706],
         [0.0118, 0.0078, 0.0118,  ..., 0.0471, 0.0588, 0.0706]],

        [[0.5765, 0.5647, 0.5529,  ..., 0.9176, 0.9137, 0.9137],
         [0.5451, 0.5333, 0.5098,  ..., 0.9137, 0.9137, 0.9137],
         [0.5412, 0.5216, 0.4863,  ..., 0.9137, 0.9137, 0.

In [27]:
from collections import defaultdict 
labelsdict3 = defaultdict(int)
for i in range(len(dataset3)):
    img, target = dataset3.__getitem__(i)
    for i in target['labels']:
        labelsdict3[i.item()] += 1
labelsdict3

defaultdict(int, {1: 6468, 3: 8230, 2: 4372, 4: 5498})

In [11]:
from torchvision.models.detection.faster_rcnn import FastRCNNPredictor
import transforms as T

def get_model(num_classes):
    # load an object detection model pre-trained on COCO
    model = torchvision.models.detection.\
           fasterrcnn_resnet50_fpn(pretrained=True)
    # get the number of input features for the classifier
    in_features = model.roi_heads.box_predictor.cls_score.in_features
    # replace the pre-trained head with a new one
    model.roi_heads.box_predictor = FastRCNNPredictor(in_features, num_classes)
   
    return model


def get_transform(train = False):
    transforms = []
    # converts the image, a PIL image, into a PyTorch Tensor
    transforms.append(T.ToTensor())
    if train:
        # during training, randomly flip the training images
        # and ground-truth for data augmentation
        transforms.append(T.RandomHorizontalFlip(0.5))
    return T.Compose(transforms)


def load_torch_model(weights_path, num_classes):    
    loaded_model = get_model(num_classes = num_classes)
    loaded_model.load_state_dict(torch.load(weights_path))
    return loaded_model

device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
# our dataset has two classes only - raccoon and not racoon
num_classes = 4
# get the model using our helper function
model = get_model(num_classes)
# move model to the right device
model.to(device)
# construct an optimizer
params = [p for p in model.parameters() if p.requires_grad]
optimizer = torch.optim.SGD(params, lr=0.005,
                            momentum=0.9, weight_decay=0.0005)
# and a learning rate scheduler which decreases the learning rate by # 10x every 5 epochs
lr_scheduler = torch.optim.lr_scheduler.StepLR(optimizer,
                                               step_size=5,
                                               gamma=0.1)

In [ ]:
import sys
sys.path.append('/Users/Administrator/DS/DeepRoad/Object_Detection')
sys.path.append('/Users/phil0/DS/DeepRoad/Object_Detection')
import utils2
from importlib import reload
reload(utils2)
from utils2 import *
        

train_fastrcnn(num_epochs = 300, model = model, optimizer = optimizer, data_loader_train = data_loader3, data_loader_val = data_loader3_test, device = device, print_freq = 50, save_every = 10, output_weights_file = 'train/weights/model_1218_fastrcnn_{}e')

(tensor([[[0.5020, 0.4980, 0.4902,  ..., 0.5529, 0.5529, 0.5529],
         [0.5020, 0.4980, 0.4980,  ..., 0.5529, 0.5529, 0.5529],
         [0.5020, 0.4980, 0.4980,  ..., 0.5529, 0.5529, 0.5529],
         ...,
         [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
         [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000],
         [0.0000, 0.0000, 0.0000,  ..., 0.0000, 0.0000, 0.0000]],

        [[0.6353, 0.6392, 0.6392,  ..., 0.6902, 0.6902, 0.6902],
         [0.6353, 0.6392, 0.6392,  ..., 0.6902, 0.6902, 0.6902],
         [0.6353, 0.6392, 0.6392,  ..., 0.6902, 0.6902, 0.6902],
         ...,
         [0.0000, 0.0000, 0.0000,  ..., 0.0039, 0.0039, 0.0000],
         [0.0000, 0.0000, 0.0000,  ..., 0.0039, 0.0039, 0.0000],
         [0.0000, 0.0000, 0.0000,  ..., 0.0039, 0.0039, 0.0000]],

        [[0.7804, 0.7804, 0.7804,  ..., 0.8000, 0.8000, 0.8000],
         [0.7804, 0.7804, 0.7804,  ..., 0.8000, 0.8000, 0.8000],
         [0.7725, 0.7804, 0.7804,  ..., 0.8000, 0.8000, 0

Epoch: [0]  [   0/2578]  eta: 0:47:14  lr: 0.000010  loss: 0.3246 (0.3246)  loss_classifier: 0.1107 (0.1107)  loss_box_reg: 0.0792 (0.0792)  loss_objectness: 0.0949 (0.0949)  loss_rpn_box_reg: 0.0399 (0.0399)  time: 1.0993  data: 0.3873  max mem: 6123
(tensor([[[0.8275, 0.7961, 0.8275,  ..., 0.4863, 0.3373, 0.4549],
         [0.7961, 0.8549, 0.7922,  ..., 0.4627, 0.4235, 0.5451],
         [0.8039, 0.7843, 0.8863,  ..., 0.4275, 0.4824, 0.5922],
         ...,
         [0.1569, 0.1647, 0.1765,  ..., 0.1098, 0.1098, 0.1059],
         [0.1608, 0.1686, 0.1765,  ..., 0.1059, 0.1020, 0.1020],
         [0.1608, 0.1686, 0.1765,  ..., 0.0980, 0.0980, 0.0941]],

        [[0.8275, 0.7961, 0.8275,  ..., 0.4510, 0.3020, 0.4157],
         [0.7961, 0.8549, 0.7882,  ..., 0.4275, 0.3882, 0.5059],
         [0.8078, 0.7804, 0.8824,  ..., 0.4000, 0.4549, 0.5647],
         ...,
         [0.1529, 0.1608, 0.1725,  ..., 0.1176, 0.1176, 0.1137],
         [0.1569, 0.1647, 0.1725,  ..., 0.1137, 0.1098, 0.1098],
  

(tensor([[[0.8588, 0.8588, 0.8588,  ..., 0.5098, 0.3765, 0.4275],
         [0.8588, 0.8588, 0.8627,  ..., 0.3961, 0.4824, 0.5961],
         [0.8588, 0.8627, 0.8627,  ..., 0.5333, 0.6039, 0.3294],
         ...,
         [0.6039, 0.6196, 0.6275,  ..., 0.1176, 0.1137, 0.1137],
         [0.5922, 0.5961, 0.5961,  ..., 0.1176, 0.1098, 0.1059],
         [0.5804, 0.5765, 0.5765,  ..., 0.1137, 0.1059, 0.1020]],

        [[0.9373, 0.9373, 0.9373,  ..., 0.5608, 0.4275, 0.4784],
         [0.9373, 0.9373, 0.9412,  ..., 0.4471, 0.5333, 0.6471],
         [0.9373, 0.9412, 0.9412,  ..., 0.5843, 0.6549, 0.3725],
         ...,
         [0.6431, 0.6588, 0.6667,  ..., 0.1647, 0.1608, 0.1608],
         [0.6314, 0.6353, 0.6353,  ..., 0.1647, 0.1569, 0.1529],
         [0.6196, 0.6157, 0.6157,  ..., 0.1608, 0.1529, 0.1490]],

        [[0.9647, 0.9647, 0.9647,  ..., 0.5255, 0.3922, 0.4431],
         [0.9647, 0.9647, 0.9686,  ..., 0.4118, 0.4980, 0.6118],
         [0.9647, 0.9686, 0.9686,  ..., 0.5569, 0.6275, 0

(tensor([[[0.5294, 0.4784, 0.4588,  ..., 0.5451, 0.5451, 0.5451],
         [0.5804, 0.5490, 0.5412,  ..., 0.5412, 0.5333, 0.5294],
         [0.6314, 0.6235, 0.6157,  ..., 0.5529, 0.5373, 0.5216],
         ...,
         [0.0039, 0.0039, 0.0039,  ..., 0.1725, 0.1765, 0.1765],
         [0.0039, 0.0039, 0.0039,  ..., 0.1922, 0.1961, 0.1882],
         [0.0039, 0.0039, 0.0039,  ..., 0.1843, 0.1922, 0.1843]],

        [[0.5843, 0.5333, 0.5137,  ..., 0.5412, 0.5412, 0.5412],
         [0.6353, 0.6039, 0.5961,  ..., 0.5373, 0.5294, 0.5255],
         [0.6863, 0.6784, 0.6706,  ..., 0.5490, 0.5333, 0.5176],
         ...,
         [0.0039, 0.0039, 0.0039,  ..., 0.1882, 0.1922, 0.1922],
         [0.0039, 0.0039, 0.0039,  ..., 0.2078, 0.2118, 0.2039],
         [0.0039, 0.0039, 0.0039,  ..., 0.2000, 0.2078, 0.2000]],

        [[0.5843, 0.5333, 0.5137,  ..., 0.4706, 0.4706, 0.4706],
         [0.6353, 0.6039, 0.5961,  ..., 0.4667, 0.4588, 0.4549],
         [0.6863, 0.6784, 0.6706,  ..., 0.4784, 0.4627, 0

(tensor([[[0.2980, 0.4118, 0.3843,  ..., 0.8392, 0.8392, 0.8392],
         [0.2980, 0.3373, 0.3098,  ..., 0.8392, 0.8392, 0.8392],
         [0.3882, 0.3216, 0.2510,  ..., 0.8392, 0.8392, 0.8392],
         ...,
         [0.2549, 0.2549, 0.2510,  ..., 0.2118, 0.1961, 0.1882],
         [0.2549, 0.2510, 0.2471,  ..., 0.2118, 0.2039, 0.2000],
         [0.2549, 0.2510, 0.2431,  ..., 0.2118, 0.2039, 0.2078]],

        [[0.2980, 0.4118, 0.3843,  ..., 0.8784, 0.8784, 0.8784],
         [0.2980, 0.3373, 0.3098,  ..., 0.8784, 0.8784, 0.8784],
         [0.3882, 0.3216, 0.2549,  ..., 0.8784, 0.8784, 0.8784],
         ...,
         [0.2471, 0.2471, 0.2431,  ..., 0.2314, 0.2157, 0.2078],
         [0.2471, 0.2431, 0.2392,  ..., 0.2314, 0.2235, 0.2196],
         [0.2471, 0.2431, 0.2353,  ..., 0.2314, 0.2235, 0.2275]],

        [[0.1961, 0.3098, 0.2824,  ..., 0.9137, 0.9137, 0.9137],
         [0.1961, 0.2353, 0.2000,  ..., 0.9137, 0.9137, 0.9137],
         [0.2784, 0.2118, 0.1333,  ..., 0.9137, 0.9137, 0

...

Epoch: [0]  [ 700/2578]  eta: 0:31:29  lr: 0.003506  loss: 0.1633 (0.1903)  loss_classifier: 0.0649 (0.0760)  loss_box_reg: 0.0667 (0.0692)  loss_objectness: 0.0207 (0.0320)  loss_rpn_box_reg: 0.0075 (0.0131)  time: 0.9989  data: 0.4208  max mem: 6146
(tensor([[[0.7529, 0.6863, 0.6980,  ..., 0.5686, 0.5686, 0.5647],
         [0.5608, 0.7412, 0.7373,  ..., 0.5686, 0.5686, 0.5647],
         [0.5569, 0.6392, 0.7333,  ..., 0.5647, 0.5647, 0.5647],
         ...,
         [0.3333, 0.2902, 0.2471,  ..., 0.1451, 0.1412, 0.1373],
         [0.2627, 0.2588, 0.2627,  ..., 0.1451, 0.1412, 0.1373],
         [0.2471, 0.2902, 0.3176,  ..., 0.1451, 0.1373, 0.1333]],

        [[0.8078, 0.7490, 0.7686,  ..., 0.6314, 0.6314, 0.6275],
         [0.6157, 0.8039, 0.8078,  ..., 0.6314, 0.6314, 0.6275],
         [0.6118, 0.7020, 0.8039,  ..., 0.6275, 0.6275, 0.6275],
         ...,
         [0.3176, 0.2745, 0.2314,  ..., 0.1451, 0.1412, 0.1373],
         [0.2471, 0.2431, 0.2471,  ..., 0.1451, 0.1412, 0.1373],
  

(tensor([[[0.9333, 0.9333, 0.9333,  ..., 1.0000, 1.0000, 1.0000],
         [0.9294, 0.9294, 0.9294,  ..., 1.0000, 1.0000, 1.0000],
         [0.9294, 0.9294, 0.9294,  ..., 1.0000, 1.0000, 1.0000],
         ...,
         [0.1451, 0.1451, 0.1490,  ..., 0.1882, 0.1804, 0.1765],
         [0.1451, 0.1451, 0.1451,  ..., 0.2000, 0.1922, 0.1882],
         [0.1451, 0.1451, 0.1451,  ..., 0.2000, 0.1961, 0.1922]],

        [[0.9608, 0.9608, 0.9608,  ..., 1.0000, 1.0000, 1.0000],
         [0.9569, 0.9569, 0.9569,  ..., 1.0000, 1.0000, 1.0000],
         [0.9569, 0.9569, 0.9569,  ..., 1.0000, 1.0000, 1.0000],
         ...,
         [0.1608, 0.1608, 0.1647,  ..., 0.2039, 0.1961, 0.1922],
         [0.1608, 0.1608, 0.1608,  ..., 0.2157, 0.2078, 0.2039],
         [0.1608, 0.1608, 0.1608,  ..., 0.2157, 0.2118, 0.2078]],

        [[0.9922, 0.9922, 0.9922,  ..., 1.0000, 1.0000, 1.0000],
         [0.9882, 0.9882, 0.9882,  ..., 1.0000, 1.0000, 1.0000],
         [0.9882, 0.9882, 0.9882,  ..., 1.0000, 1.0000, 1

(tensor([[[0.4902, 0.6314, 0.8588,  ..., 0.7686, 0.7686, 0.7686],
         [0.6235, 0.6667, 0.8549,  ..., 0.7686, 0.7686, 0.7686],
         [0.7373, 0.7647, 0.8941,  ..., 0.7725, 0.7686, 0.7686],
         ...,
         [0.6000, 0.6000, 0.6000,  ..., 0.3490, 0.3490, 0.3451],
         [0.5922, 0.5961, 0.5961,  ..., 0.3451, 0.3412, 0.3412],
         [0.5882, 0.5922, 0.5922,  ..., 0.3412, 0.3373, 0.3373]],

        [[0.4863, 0.6275, 0.8549,  ..., 0.8157, 0.8157, 0.8157],
         [0.6196, 0.6627, 0.8510,  ..., 0.8157, 0.8157, 0.8157],
         [0.7373, 0.7647, 0.8941,  ..., 0.8196, 0.8157, 0.8157],
         ...,
         [0.5412, 0.5412, 0.5412,  ..., 0.3451, 0.3451, 0.3412],
         [0.5333, 0.5373, 0.5373,  ..., 0.3412, 0.3373, 0.3373],
         [0.5294, 0.5333, 0.5333,  ..., 0.3373, 0.3333, 0.3333]],

        [[0.5059, 0.6471, 0.8745,  ..., 0.8706, 0.8706, 0.8706],
         [0.6392, 0.6824, 0.8706,  ..., 0.8706, 0.8706, 0.8706],
         [0.7451, 0.7725, 0.9020,  ..., 0.8745, 0.8706, 0

(tensor([[[0.6275, 0.5843, 0.5647,  ..., 0.0627, 0.0471, 0.0392],
         [0.6235, 0.5804, 0.5608,  ..., 0.0627, 0.0471, 0.0353],
         [0.6157, 0.5804, 0.5608,  ..., 0.0627, 0.0431, 0.0275],
         ...,
         [0.0000, 0.0000, 0.0000,  ..., 0.1020, 0.0941, 0.0941],
         [0.0000, 0.0000, 0.0000,  ..., 0.0941, 0.0863, 0.0824],
         [0.0000, 0.0000, 0.0000,  ..., 0.0902, 0.0784, 0.0745]],

        [[0.6039, 0.5608, 0.5412,  ..., 0.0667, 0.0510, 0.0392],
         [0.6000, 0.5569, 0.5373,  ..., 0.0667, 0.0510, 0.0353],
         [0.5922, 0.5569, 0.5373,  ..., 0.0667, 0.0471, 0.0314],
         ...,
         [0.0000, 0.0000, 0.0000,  ..., 0.1216, 0.1137, 0.1059],
         [0.0000, 0.0000, 0.0000,  ..., 0.1137, 0.1059, 0.0941],
         [0.0000, 0.0000, 0.0000,  ..., 0.1098, 0.0980, 0.0863]],

        [[0.3686, 0.3255, 0.3059,  ..., 0.0824, 0.0588, 0.0471],
         [0.3647, 0.3216, 0.3020,  ..., 0.0824, 0.0667, 0.0431],
         [0.3490, 0.3137, 0.2941,  ..., 0.0824, 0.0627, 0

(tensor([[[0.4471, 0.4784, 0.5098,  ..., 0.8980, 0.8941, 0.8941],
         [0.4118, 0.4471, 0.4863,  ..., 0.8980, 0.8941, 0.8941],
         [0.3882, 0.4235, 0.4706,  ..., 0.9020, 0.8980, 0.8980],
         ...,
         [0.2078, 0.2078, 0.2039,  ..., 0.0549, 0.0863, 0.1451],
         [0.1608, 0.1608, 0.1608,  ..., 0.0941, 0.1843, 0.2745],
         [0.0471, 0.0471, 0.0549,  ..., 0.2784, 0.2941, 0.3098]],

        [[0.5255, 0.5569, 0.5882,  ..., 0.9765, 0.9725, 0.9725],
         [0.4902, 0.5255, 0.5647,  ..., 0.9765, 0.9725, 0.9725],
         [0.4667, 0.5020, 0.5490,  ..., 0.9804, 0.9765, 0.9765],
         ...,
         [0.2431, 0.2431, 0.2392,  ..., 0.0706, 0.1020, 0.1608],
         [0.2000, 0.2000, 0.2000,  ..., 0.1098, 0.2000, 0.2902],
         [0.0941, 0.0941, 0.1020,  ..., 0.2941, 0.3098, 0.3255]],

        [[0.5176, 0.5490, 0.5804,  ..., 0.9725, 0.9686, 0.9686],
         [0.4824, 0.5176, 0.5569,  ..., 0.9725, 0.9686, 0.9686],
         [0.4588, 0.4941, 0.5412,  ..., 0.9765, 0.9725, 0